In [128]:
import csv
import random
import re
import time
import psycopg2
import itertools
# import csv_utils
import requests
import bs4
from unidecode import unidecode

CSV_FILE_ENCODING = 'utf-8'
# global municodemap
# global current_muni
# global MUNI_PARCELID_LIST_FILE
# global muni_idbase_map
# global ID_BASE
# global TEST_PARID_FILE

def main():
    # for accessing a list of all parcelIDs by with one muni's list per file
    # global INPUT_FILE
    # INPUT_FILE = 'workspace/pitcairnparids.csv'

    # parcels whose base property data is not written are written here before moving on
    global LOG_FILE
    LOG_FILE = 'output/swissvaleerror.csv'

    # this log file is used for storing parcels whose person and propertyperson inserts fail
    global LOG_FILE_AUX
    LOG_FILE_AUX = 'output/swissvaleerror_aux.csv'

    # ID number of the system user connected to these original inserts
    # user 99 is sylvia, our COG robot
    global UPDATING_USER_ID
    UPDATING_USER_ID = 99

    global PARID_FILE
    # PARID_FILE = 'parcelidlists/wilmerdingparids.csv'
    # PARID_FILE = 'parcelidlists/parcelidstest.csv'
    #PARID_FILE = 'parcelidlists/pitcairnparids_correct.csv'
    #PARID_FILE = 'parcelidlists/eastmckeesportparids.csv'
    #PARID_FILE = 'parcelidlists/wilkinsparcelids.csv'
    #PARID_FILE = 'parcelidlists/chalfantparcelids.csv'
    PARID_FILE = 'parcelidlists/swissvaleparcelids.csv'
    
    # used as the access key for muni codes and ID bases in the dictionaries below
    global current_muni
    current_muni = 'swissvale'

    # use as floor value for all new propertyIDs
    global PROP_ID_BASE
    PROP_ID_BASE = 100000

    # floor value for new personIDs
    global PERSON_ID_BASE
    PERSON_ID_BASE = 10000

    # used for sliding starting ID up to accommodate a parcelid list adjustment due to errors on pesky parcels
    # must be manually set if there's an error: start one above the most recently issued ID
    # this gets added to the base ID in the ID range generation methods
    global BUMP_UP
    BUMP_UP = 0

    global municodemap
    municodemap = {'chalfant':814,'churchhill':816, 'eastmckeesport':821, 'pitcairn':847, 'wilmerding':867, 'wilkins':953, 'cogland':999, 'swissvale':111}

    # add these base amounts to the universal base to get starting IDs
    global muni_idbase_map
    muni_idbase_map = {'chalfant':10000,'churchhill':20000, 'eastmckeesport':30000, 'pitcairn':40000, 'wilmerding':0, 'wilkins':50000, 'cogland':60000, 'swissvale':70000}

    # add these base amounts to the universal base to get starting IDs
    global person_idbase_map
    person_idbase_map = {'chalfant':10000,'churchhill':20000, 'eastmckeesport':30000, 'pitcairn':40000, 'wilmerding':0, 'wilkins':50000, 'cogland':60000, 'swissvale':70000}

    # jump into the actual work here
    insert_property_basetableinfo()
    
    # Add owner data to properties
    # properties_with_owner_info = add_prop_info(properties)
    # Save new CSV file with property plus owner data
    # OUTPUT_FILE = 'output/testPropOut.txt'
    # save_properties_as_csv(properties_with_owner_info, OUTPUT_FILE)

def get_nextpropertyid(munioffset):
    # consider a range multiplier by municipality to generate starting 
    # at, say 110000 and the next at 120000 which allows for non-overlapping
    #ids for munis with a property count of up to 10000
    for i in list(range(PROP_ID_BASE + munioffset + BUMP_UP, PROP_ID_BASE + munioffset + 9999)):
        yield i;

def get_nextpersonid(munioffset):
    for i in list(range(PERSON_ID_BASE + munioffset + BUMP_UP, PERSON_ID_BASE + munioffset + 9999)):
        yield i;



def get_nextparcelid(input_file):
    # Read the CSV file and iterate through every property
    with open(input_file, 'r', encoding=CSV_FILE_ENCODING) as csv_file:
        reader = csv.DictReader(csv_file)
        for row in reader:
            parid = str(row['parcelid']).strip()
            yield parid



In [129]:
db_conn = None
def get_db_conn():
    global db_conn
    if db_conn is not None:
        return db_conn
    db_conn = psycopg2.connect(
        dbname="cogdb",
        user="matts207",
        password="12345",
        host="localhost"
    )
    return db_conn




In [130]:
def logerror(parcelid):
    with open(LOG_FILE, 'a', encoding=CSV_FILE_ENCODING) as outfile:
        writer = csv.writer(outfile)
        writer.writerow([parcelid])

def logerror_aux(parcelid):
    with open(LOG_FILE_AUX, 'a', encoding=CSV_FILE_ENCODING) as outfile:
        writer = csv.writer(outfile)
        writer.writerow([parcelid])

# for debugging and transferability purposes
def save_properties_as_csv(properties_with_owner_info, output_file):
    fieldnames = None
    with open(output_file, 'w', encoding=CSV_FILE_ENCODING) as outfile:
        writer = csv.writer(outfile)
        for prop in properties_with_owner_info:
            if fieldnames is None:
                fieldnames = sorted(prop.keys())
                writer.writerow(fieldnames)
            writer.writerow([prop[k] for k in fieldnames])


In [131]:
def connect_person_to_property(propertyid, personid):
    db_conn = get_db_conn()
    cursor = db_conn.cursor()

    insert_sql = """
        INSERT INTO public.propertyperson(
            property_propertyid, person_personid)
    VALUES (%(prop)s, %(pers)s);
    """
    insertmap = {}
    
    # load up vars for use in SQL from each of the parse methods
    insertmap['prop'] = propertyid
    insertmap['pers'] = personid

    cursor.execute(insert_sql, insertmap)
    db_conn.commit()
    print('----- connected person owner to property -----')

def create_and_insert_unitzero(propertyid):
    db_conn = get_db_conn()
    cursor = db_conn.cursor()
    
    insert_sql = """
        INSERT INTO public.propertyunit(
            unitid, unitnumber, property_propertyid, otherknownaddress, notes, 
            rental)
        VALUES (DEFAULT, '0', %(property_propertyid)s, NULL, 
            'robot-generated unit representing the primary habitable dwelling on a property', 
            FALSE);
    """
    insertmap = {}
    
    # load up vars for use in SQL from each of the parse methods
    insertmap['property_propertyid'] = propertyid

    cursor.execute(insert_sql, insertmap)
    db_conn.commit()
    print('----- built unit zero -----')


# deprecated from Daniel--kept in as a reference
def add_prop_info(properties):
    PARCEL_ID_FIELD = 'parcelid'
    OWNER_NAME_FIELD = 'OwnerName'
    OWNER_ADDRESS_FIELD = 'OwnerAddress'
    for prop in properties:
        assert prop[PARCEL_ID_FIELD]  # Every property must have a parcel id
        parcel_id = prop[PARCEL_ID_FIELD]
        print('Processing parcel', parcel_id)

        # Get the html from the county's website
        property_html = get_county_page_for(parcel_id)

        # Wait between request, just to be nice with the county's site
        sleep_time = random.random() * 3  # Sleep at most 3 seconds
        time.sleep(sleep_time)
        print('sleeping for {:.2f} seconds'.format(sleep_time))

        # Add owner name and address to the property
        prop[OWNER_NAME_FIELD] = extract_owner_name(parcel_id, property_html)
        prop[OWNER_ADDRESS_FIELD] = extract_owner_address(
                parcel_id, property_html)
        print(prop[OWNER_NAME_FIELD], prop[OWNER_ADDRESS_FIELD])

        yield prop


county_info_cache = {}
def get_county_page_for(parcel_id):
    if parcel_id in county_info_cache:
        return county_info_cache[parcel_id]
    COUNTY_REAL_ESTATE_URL = ('http://www2.county.allegheny.pa.us/'
                              'RealEstate/GeneralInfo.aspx?')
    search_parameters = {
        'ParcelID': parcel_id,
        'SearchType': 3,
        'SearchParcel': parcel_id}
    waittime = random.uniform(0.0,1.0)
    print("waiting:" + str(waittime))
    time.sleep(waittime)
    try:
        response = requests.get(
                COUNTY_REAL_ESTATE_URL,
                params=search_parameters,
                timeout=5)
        print('Scraping data from county: %s' + parcel_id)
    except requests.exceptions.Timeout:
        # Wait 10 secs and try one more time
        time.sleep(10)
        response = requests.get(
                COUNTY_REAL_ESTATE_URL,
                params=search_parameters,
                timeout=5)
    county_info_cache[parcel_id] = response.text
    return response.text

#---------------------------------------------
#           HTML SCRAPING METHODS
#---------------------------------------------

def extract_lotandblock_fromparid(parid):
    trimmedparid = parid[0:11]
    exp = re.compile(r'([1-9]+)(\w)[0]*([1-9]+)')
    gl = re.search(exp, trimmedparid)
    if(gl):
        lob = gl.group(1) + '-' + gl.group(2) + '-' + gl.group(3)
        return lob
    else:
        print('ERROR: LOB parsing')
        return ''

def extract_owner_name(property_html):
    OWNER_NAME_SPAN_ID = 'BasicInfo1_lblOwner'
    persondict = {}

    soup = bs4.BeautifulSoup(property_html, 'lxml')
    owner_full_name = soup.find('span', id=OWNER_NAME_SPAN_ID).text
    print('owner_raw_name:' + str(owner_full_name))
    # Remove extra spaces from owner's name
    full_owners = re.sub(r'\s+', ' ', owner_full_name.strip())
    
    #exp = re.compile(r'(\w+|[&])\s+(\w+|[&])\s*(\w*|[&]).*')
    #namegroups = re.search(exp, owner_full_name)
    #print(len(namegroups.groups()))
    #persondict['lname'] = str(namegroups.group(1)).title()
    
    #if len(namegroups.groups()) == 2:
        #persondict['fname'] = str(namegroups.group(2)).title()
    #elif len(namegroups.groups()) == 3:
        #persondict['fname'] = str(namegroups.group(2)).title() + ' ' + str(namegroups.group(3)).title()

    #print(str(persondict['fname']) + ' ' + str(persondict['lname']))
    
    return full_owners

def extract_propertyaddress(parcel_id, property_html):
    propaddrmap = {}
    PROP_ADDR_SPAN_ID = 'BasicInfo1_lblAddress'
    # print(property_html)
    soup = bs4.BeautifulSoup(property_html, 'lxml')
    
    # this yeilds something like
    # 471&nbsp;WALNUT  ST<br>PITTSBURGH,&nbsp;PA&nbsp;15238
    prop_addr_raw = soup.find('span', id=PROP_ADDR_SPAN_ID).text
    scrapedhtml = soup.select("#BasicInfo1_lblAddress")

    print("Scraped:" + str(scrapedhtml))
    soup = bs4.BeautifulSoup(str(scrapedhtml), 'lxml')
    adrlistraw = soup.span.contents 
    # make sure we have all the parts of the address
    if len(adrlistraw) < 3:
        print("Raising Exception in extract_propertyaddress")
        raise Exception
    
    street = re.sub('  ', ' ', adrlistraw[0])
    propaddrmap['street'] = str(unidecode(street)).strip()
    print(propaddrmap['street'])
    # on the city, state, zip line, grab until the comma before the state
    exp = re.compile('[^,]*')
    propaddrmap['city'] = exp.search(adrlistraw[2]).group()
    print("city:" + propaddrmap['city'])
    # hard-code pa
    propaddrmap['state']= 'PA'
    # zip is just the last 5 chars    
    propaddrmap['zipc'] = adrlistraw[2][-5:]
    print("Zip:" + propaddrmap['zipc'])

    return propaddrmap

def extract_owneraddress(property_html):
    print('--------- extracting owner address ------------')
    owneraddrmap = {}
    # print(property_html)
    soup = bs4.BeautifulSoup(property_html, 'lxml')
    # this yeilds something like
    # 471&nbsp;WALNUT  ST<br>PITTSBURGH,&nbsp;PA&nbsp;15238
    scrapedhtml = soup.select("#lblChangeMail")
    owneraddrmap['notes_adrdump'] = str(scrapedhtml)

    print("Scraped:" + str(scrapedhtml))
    soup = bs4.BeautifulSoup(str(scrapedhtml), 'lxml')
    # this spits out a three-item list. We throw away the <br> which is 
    # the middle item. The first is the street, the second gets chopped up
    adrlistraw = soup.span.contents 
    print(adrlistraw)
    # make sure we have all the parts of the address
    if len(adrlistraw) < 3:
        print("Raising Exception")
        raise Exception
    
    owneraddrmap['thirdline'] = None
    addrlistindex = 0
    if len(adrlistraw) > 3:
        print("Extra line address")
        thirdline = re.sub('  ', ' ', adrlistraw[addrlistindex])
        owneraddrmap['thirdline'] = str(unidecode(thirdline)).strip()
        addrlistindex += 2
        
    print("dgjalksdjgdsag")
    ownerstreet = re.sub('  ', ' ', adrlistraw[addrlistindex])
    owneraddrmap['street'] = str(unidecode(ownerstreet)).strip()
    print(owneraddrmap['street'])
    # on the city, state, zip line, grab until the comma before the state
    exp = re.compile('[^,]*')
    addrlistindex += 2
    owneraddrmap['city'] = exp.search(adrlistraw[addrlistindex]).group()
    print("city:" + owneraddrmap['city'])
    # grap with string indexes (fragile if there is more than one space before zip)
    # TODO: use regexp
    exp=re.compile(r',\s*(\w\w)')
    m = re.search(exp,adrlistraw[addrlistindex])
    owneraddrmap['state'] = str(m.group(1))
    
    # abandoned string slicing approach (too brittle; use regexp)
    # owneraddrmap['state']= adrlistraw[2][-13:-11]
    print("state:" + owneraddrmap['state'])
    
    # owner zips could come in as: 15218 OR 15218- OR 15218-2342
    # just lose the routing numbers and take the first digits until the -
    exp=re.compile(r'\d+')
    m = re.search(exp, adrlistraw[addrlistindex])
    owneraddrmap['zipc'] = str(m.group())

    # another abandoned string slicing approach: 
    # also too brittle given range of scraped inputs
    # owneraddrmap['zip'] = adrlistraw[2][-10:]
    print("zip:" + owneraddrmap['zipc'])

    return owneraddrmap


def extact_owner_name_and_mailing(parcel_id, property_html):

    OWNER_ADDRESS_SPAN_ID = 'lblChangeMail'
    addrparts = {}

    soup = bs4.BeautifulSoup(property_html, 'lxml')
    owner_address_raw = soup.find('span', id=OWNER_ADDRESS_SPAN_ID).text
    # Remove extra spaces
    addrparts['addr'] = rs.sub('')

    owner_address = re.sub(r'\s+', ' ', owner_address.strip())
    # Remove leading spaces before commas
    owner_address = re.sub(r'\s+,', ',', owner_address)

    return owner_address


def extract_propertyusetype(property_html):
    USE_TYPE_SPAN_ID = 'lblUse'

    soup = bs4.BeautifulSoup(property_html, 'lxml')
    usetype = soup.find('span', id=USE_TYPE_SPAN_ID).text
    # Remove extra spaces
    usetype = re.sub(r'\s+', ' ', usetype.strip())
    # Remove leading spaces before commas
    usetype = str(re.sub(r'\s+,', ',', usetype)).title()
    return usetype

def extract_class(property_html):
    CLASS_SPAN_ID = 'lblState'

    soup = bs4.BeautifulSoup(property_html, 'lxml')
    propclass = soup.find('span', id=CLASS_SPAN_ID).text
    # Remove extra spaces
    propclass = re.sub(r'\s+', ' ', propclass.strip())
    # Remove leading spaces before commas
    propclass = str(re.sub(r'\s+,', ',', propclass)).title()
    return propclass

def extract_ownercode(property_html):
    OWNER_CODE_SPAN_ID = 'lblOwnerCode'

    soup = bs4.BeautifulSoup(property_html, 'lxml')
    ownercode = soup.find('span', id=OWNER_CODE_SPAN_ID).text
    # Remove extra spaces
    ownercode = re.sub(r'\s+', ' ', ownercode.strip())
    # Remove leading spaces before commas
    ownercode = str(re.sub(r'\s+,', ',', ownercode)).title()
    return ownercode

def check_current_owner(parcelid):
    namemap = {}
    get_propid = "SELECT propertyid FROM public.property WHERE parid=%(parcelid)s;"
    inserts = {}
    inserts['parcelid'] = parcelid
    db_conn = get_db_conn()
    cursor = db_conn.cursor()
    cursor.execute(get_propid, inserts)
    propidlist = cursor.fetchall()
    propid = propidlist[0][0]
    get_personid = "SELECT person_personid FROM public.propertyperson WHERE property_propertyid=%(property_propertyid)s;"
    inserts['property_propertyid'] = propid
    cursor.execute(get_personid, inserts)
    personidlist = cursor.fetchall()
    personid = personidlist[0][0]
    get_names = "SELECT fname, lname FROM public.person WHERE personid=%(personid)s"
    inserts['personid'] = personid
    cursor.execute(get_names, inserts)
    names = cursor.fetchall()
    print(names)
    namemap['fname'] = names[0][0]
    namemap['lname'] = names[0][1]
    return namemap


In [132]:
def extract_and_insert_person(rawhtml, propertyid, personid, propinserts):
    # fixed values specific to keys in lookup tables
    

    db_conn = get_db_conn()
    cursor = db_conn.cursor()

    notemsg = """In case of confusion, check autmated record entry with raw text from the county database:"""

    insert_sql = """
        INSERT INTO public.person(
            personid, persontype, muni_municode, fname, lname, jobtitle, 
            phonecell, phonehome, phonework, email, address_street, address_city, 
            address_state, address_zip, notes, lastupdated, expirydate, isactive, 
            isunder18, humanverifiedby,compositelname, mailing_address_street, mailing_address_city,
            mailing_address_state, mailing_address_zip, useseparatemailingaddr, mailing_address_thirdline)
    VALUES (%(personid)s, cast ( 'ownercntylookup' as persontype), 
            %(muni_municode)s, NULL, %(lname)s, 'Property Owner', 
            NULL, NULL, NULL, NULL, %(address_street)s, %(address_city)s, 
            %(address_state)s, %(address_zip)s, %(notes)s, now(), NULL, TRUE, 
            FALSE, NULL, true, %(mailing_street)s, %(mailing_city)s, %(mailing_state)s, %(mailing_zip)s,
            %(mailingsameasres)s, %(thirdline)s);
    """
    
    
    insertmap = {}
    
    # load up vars for use in SQL from each of the parse methods
    insertmap['personid'] = personid
    print("personid:"+str(insertmap['personid']))
    insertmap['muni_municode'] = str(municodemap[current_muni])
    
    insertmap['mailing_street'] = None
    insertmap['mailing_city'] = None
    insertmap['mailing_state'] = None
    insertmap['mailing_zip'] = None
    insertmap['thirdline'] = None
    insertmap['mailingsameasres'] = 'true'
    
    try:
        ownername = extract_owner_name(rawhtml)
        insertmap['lname'] = ownername
        print('extracted owner:' + insertmap['lname'] )

    except Exception:
        print("Malformed owner name at e and i person")
        print("ERROR malformed address at:" + str(propertyid))
    
    try:
        owneraddrmap = extract_owneraddress(rawhtml)
        print("ARE THEY THE SAME??? " + str(owneraddrmap['street'] == propinserts['street']) + owneraddrmap['street'] + propinserts['street'])
        print(propinserts)
        if owneraddrmap['street'] == propinserts['street']:
            print("SAME ADDRESS")
            insertmap['address_street'] = owneraddrmap['street']
            insertmap['address_city'] = owneraddrmap['city']
            insertmap['address_state'] = owneraddrmap['state']
            insertmap['address_zip'] = owneraddrmap['zipc']
            insertmap['notes'] = notemsg + ownername + " Raw Address: " + owneraddrmap['notes_adrdump']
        else:
            print("DIFFERENT MAILING")
            insertmap['address_street'] = None
            insertmap['address_city'] = None
            insertmap['address_state'] = None
            insertmap['address_zip'] = None
            insertmap['mailing_street'] = owneraddrmap['street']
            insertmap['mailing_city'] = owneraddrmap['city']
            insertmap['mailing_state'] = owneraddrmap['state']
            insertmap['mailing_zip'] = owneraddrmap['zipc']
            print(11)
            insertmap['thirdline'] = owneraddrmap['thirdline']
            print(22)
            insertmap['mailingsameasres'] = 'false'
            insertmap['notes'] = notemsg + ownername + " Raw address: " + owneraddrmap['notes_adrdump']
            print(insertmap['thirdline'])
            print(insertmap['notes'])

    except Exception:
        print("NO MAILING")
        insertmap['address_street'] = propinserts['street']
        insertmap['address_city'] = propinserts['city']
        insertmap['address_state'] = propinserts['state']
        insertmap['address_zip'] = propinserts['zipc']
        insertmap['notes'] = "Owner does not have mailing address"

        
    print(insertmap['mailing_zip'])
    if insertmap['address_street']:
        print('extracted owner address:' \
            + ' ' + insertmap['address_street'] \
            + ' ' + insertmap['address_city'] \
            + ', ' + insertmap['address_state'] \
            + ' ' + insertmap['address_zip'])
    if insertmap['mailing_street']:
        print('extracted mailing address:' \
            + ' ' + insertmap['mailing_street'] \
            + ' ' + insertmap['mailing_city'] \
            + ', ' + insertmap['mailing_state'] \
            + ' ' + insertmap['mailing_zip'] )
    
    print('Inserting person data for id: %s' % (insertmap['personid']))
    print('person notes:' + insertmap['notes'])
    
    cursor.execute(insert_sql, insertmap)
    db_conn.commit()
    print('----- committed person owner -----')
    # commit core propertytable insert


In [133]:
def insert_property_basetableinfo():
    db_conn = get_db_conn()
    cursor = db_conn.cursor()
    parcelgenerator = get_nextparcelid(PARID_FILE)
    propertyidgenerator = get_nextpropertyid(muni_idbase_map[current_muni])
    personidgenerator = get_nextpersonid(person_idbase_map[current_muni])

    # user 99 is the cog robot, Sylvia
    insert_sql = """
        INSERT INTO public.property(
            propertyid, municipality_municode, parid, address, 
            notes, addr_city, addr_state, addr_zip,
            lotandblock, propclass, propertyusetype, ownercode,
            lastupdated, lastupdatedby)
        VALUES (%(propid)s, %(muni)s, %(parcelid)s, %(addr)s, 
                %(notes)s, %(city)s, %(state)s, %(zipcode)s,
                %(lotandblock)s, %(propclass)s, %(propertyusetype)s, %(ownercode)s,
                now(), %(updatinguser)s);

    """
    insertmap = {}
    propertycount = 0
    personcount = 0
    # the main delegator loop
    for parid in parcelgenerator:
        # go get raw HTML
        rawhtml = get_county_page_for(parid)
        
        # load up vars for use in SQL from each of the parse methods
        insertmap['propid'] = next(propertyidgenerator)
        propid = insertmap['propid']
        print("newid:"+ str(propid))
        # parid comes from the iterated item variable parid
        insertmap['parcelid'] = parid
        insertmap['muni'] = municodemap[current_muni]
        try:
            addrmap = extract_propertyaddress(parid, rawhtml)
        except Exception:
            print("MA base table")
            print("ERR malformed address at:" + parid)
            logerror(parid)
            continue
        insertmap['addr'] = addrmap['street']
        insertmap['notes'] = 'core data scraped from county site'
        insertmap['city'] = addrmap['city']
        insertmap['state'] = addrmap['state']
        insertmap['zipcode'] = addrmap['zipc']   
        insertmap['lotandblock'] = extract_lotandblock_fromparid(parid)
        # print('lob:' + insertmap['lotandblock'])

        insertmap['propclass'] = str(extract_class(rawhtml))
        # print('class:' + insertmap['propclass'])

        insertmap['propertyusetype'] = extract_propertyusetype(rawhtml)
        # print('use:' + insertmap['propertyusetype'])

        insertmap['ownercode'] = extract_ownercode(rawhtml)
        # print('owner code:' + insertmap['ownercode'])

        insertmap['updatinguser'] = str(99)
        # print('updater id:' + insertmap['updatinguser'])

        print('Inserting parcelid data: %s' % (parid))
        
        try:
            # execute insert on property table
            cursor.execute(insert_sql, insertmap)
            # commit core propertytable insert
            db_conn.commit()
            propertycount = propertycount + 1
            print('----- committed property core table -----')
        except:
            print('ERROR: unable to insert base property data...skipping\n')
            print('********* MOVING ON ********************')
            logerror_aux(parid)
            continue
        try:
        # this try catches soup related errors
        # and sql errors bubbling up from the extraction methods that also commit
            personid = next(personidgenerator)
            print(1)
            extract_and_insert_person(rawhtml, propid, personid, addrmap)
            print(2)
            connect_person_to_property(propid, personid)
            print(3)
            personcount = personcount + 1
        except:
            print('ERROR: unable to extract, commit, or connect person owner\n')
            logerror_aux(parid)
            continue
        try:
            # create standard unit number 0 for each property in system
            create_and_insert_unitzero(propid)
        except:
            print('ERROR: unable to create unit zero for property no.\n'+ str(propid))
            logerror(parid)
            continue
        print('--------- running totals --------')
        print('Props inserted: ' + str(propertycount))
        print('Persons inserted: ' + str(personcount))
        print('********** DONE! *************\n')

        # run insert with sql statement all loaded up
    cursor.close()
    db_conn.close()
    print('Count of properties inserted: ' + str(propertycount))
    print('Count of persons inserted: ' + str(personcount))

# db debugging--don't forget conn.commit!
    # newid = insertmap['id']
    #     selectsql = """
    #         SELECT * from property;
    #     """
    #     cursor.execute(selectsql)
    #     print(cursor.fetchone())




In [134]:
if __name__ == '__main__':
    main()


waiting:0.4868417924000591
Scraping data from county: %s0177P00118000000
newid:170000
Scraped:[<span class="Data" id="BasicInfo1_lblAddress">7241 PRINCETON  PL<br/>PITTSBURGH, PA 15218</span>]
7241 PRINCETON PL
city:PITTSBURGH
Zip:15218
Inserting parcelid data: 0177P00118000000
----- committed property core table -----
1
personid:80000
owner_raw_name:TRUDEAU JOHN B     WESTCOTT JAY 
extracted owner:TRUDEAU JOHN B WESTCOTT JAY
--------- extracting owner address ------------
Scraped:[<span class="DATA" id="lblChangeMail">7241 PRINCETON PL <br/>PITTSBURGH , PA 15218-2038</span>]
['7241\xa0PRINCETON\xa0PL\xa0', <br/>, 'PITTSBURGH\xa0,\xa0PA\xa015218-2038']
dgjalksdjgdsag
7241 PRINCETON PL
city:PITTSBURGH 
state:PA
zip:15218
ARE THEY THE SAME??? True7241 PRINCETON PL7241 PRINCETON PL
{'street': '7241 PRINCETON PL', 'city': 'PITTSBURGH', 'state': 'PA', 'zipc': '15218'}
SAME ADDRESS
None
extracted owner address: 7241 PRINCETON PL PITTSBURGH , PA 15218
Inserting person data for id: 80000
perso

Scraping data from county: %s0177S00064000000
newid:170006
Scraped:[<span class="Data" id="BasicInfo1_lblAddress">7912 NEWMEYER  ST<br/>PITTSBURGH, PA 15218</span>]
7912 NEWMEYER ST
city:PITTSBURGH
Zip:15218
Inserting parcelid data: 0177S00064000000
----- committed property core table -----
1
personid:80006
owner_raw_name:BARTLETT DAVID MC AFEE     
extracted owner:BARTLETT DAVID MC AFEE
--------- extracting owner address ------------
Scraped:[<span class="DATA" id="lblChangeMail">7912 NEWMEYER ST <br/>PITTSBURGH , PA 15218-1828</span>]
['7912\xa0NEWMEYER\xa0ST\xa0', <br/>, 'PITTSBURGH\xa0,\xa0PA\xa015218-1828']
dgjalksdjgdsag
7912 NEWMEYER ST
city:PITTSBURGH 
state:PA
zip:15218
ARE THEY THE SAME??? True7912 NEWMEYER ST7912 NEWMEYER ST
{'street': '7912 NEWMEYER ST', 'city': 'PITTSBURGH', 'state': 'PA', 'zipc': '15218'}
SAME ADDRESS
None
extracted owner address: 7912 NEWMEYER ST PITTSBURGH , PA 15218
Inserting person data for id: 80006
person notes:In case of confusion, check autmated r

Scraping data from county: %s0178C00141000000
newid:170012
Scraped:[<span class="Data" id="BasicInfo1_lblAddress">1918 MONONGAHELA  AVE<br/>PITTSBURGH, PA 15218</span>]
1918 MONONGAHELA AVE
city:PITTSBURGH
Zip:15218
Inserting parcelid data: 0178C00141000000
----- committed property core table -----
1
personid:80012
owner_raw_name:MARTINO RUDOLPH     
extracted owner:MARTINO RUDOLPH
--------- extracting owner address ------------
Scraped:[<span class="DATA" id="lblChangeMail">1918 MONONGAHELA AVE <br/>PITTSBURGH , PA 15218-2473</span>]
['1918\xa0MONONGAHELA\xa0AVE\xa0', <br/>, 'PITTSBURGH\xa0,\xa0PA\xa015218-2473']
dgjalksdjgdsag
1918 MONONGAHELA AVE
city:PITTSBURGH 
state:PA
zip:15218
ARE THEY THE SAME??? True1918 MONONGAHELA AVE1918 MONONGAHELA AVE
{'street': '1918 MONONGAHELA AVE', 'city': 'PITTSBURGH', 'state': 'PA', 'zipc': '15218'}
SAME ADDRESS
None
extracted owner address: 1918 MONONGAHELA AVE PITTSBURGH , PA 15218
Inserting person data for id: 80012
person notes:In case of confu

Scraping data from county: %s0234J00166000000
newid:170017
Scraped:[<span class="Data" id="BasicInfo1_lblAddress">8206 WESTMORELAND  AVE<br/>PITTSBURGH, PA 15218</span>]
8206 WESTMORELAND AVE
city:PITTSBURGH
Zip:15218
Inserting parcelid data: 0234J00166000000
----- committed property core table -----
1
personid:80017
owner_raw_name:IDUCOVICH KATHLEEN S     
extracted owner:IDUCOVICH KATHLEEN S
--------- extracting owner address ------------
Scraped:[<span class="DATA" id="lblChangeMail">8206 WESTMORELAND AVE <br/>PITTSBURGH , PA 15218-1725</span>]
['8206\xa0WESTMORELAND\xa0AVE\xa0', <br/>, 'PITTSBURGH\xa0,\xa0PA\xa015218-1725']
dgjalksdjgdsag
8206 WESTMORELAND AVE
city:PITTSBURGH 
state:PA
zip:15218
ARE THEY THE SAME??? True8206 WESTMORELAND AVE8206 WESTMORELAND AVE
{'street': '8206 WESTMORELAND AVE', 'city': 'PITTSBURGH', 'state': 'PA', 'zipc': '15218'}
SAME ADDRESS
None
extracted owner address: 8206 WESTMORELAND AVE PITTSBURGH , PA 15218
Inserting person data for id: 80017
person not

Scraping data from county: %s0177K00021000000
newid:170023
Scraped:[<span class="Data" id="BasicInfo1_lblAddress">1424 MACON  AVE<br/>PITTSBURGH, PA 15218</span>]
1424 MACON AVE
city:PITTSBURGH
Zip:15218
Inserting parcelid data: 0177K00021000000
----- committed property core table -----
1
personid:80023
owner_raw_name:SHORT STEPHANIE A     ENGLISH COREY J 
extracted owner:SHORT STEPHANIE A ENGLISH COREY J
--------- extracting owner address ------------
Scraped:[<span class="DATA" id="lblChangeMail">1424 MACON AVE <br/>PITTSBURGH , PA 15218-1221</span>]
['1424\xa0MACON\xa0AVE\xa0', <br/>, 'PITTSBURGH\xa0,\xa0PA\xa015218-1221']
dgjalksdjgdsag
1424 MACON AVE
city:PITTSBURGH 
state:PA
zip:15218
ARE THEY THE SAME??? True1424 MACON AVE1424 MACON AVE
{'street': '1424 MACON AVE', 'city': 'PITTSBURGH', 'state': 'PA', 'zipc': '15218'}
SAME ADDRESS
None
extracted owner address: 1424 MACON AVE PITTSBURGH , PA 15218
Inserting person data for id: 80023
person notes:In case of confusion, check autmat

...

Scraping data from county: %s0178L00181000000
newid:173539
Scraped:[<span class="Data" id="BasicInfo1_lblAddress">7310 DENNISTON  AVE<br/>PITTSBURGH, PA 15218</span>]
7310 DENNISTON AVE
city:PITTSBURGH
Zip:15218
Inserting parcelid data: 0178L00181000000
----- committed property core table -----
1
personid:83533
owner_raw_name:DORSEY ROMANZA M     
extracted owner:DORSEY ROMANZA M
--------- extracting owner address ------------
Scraped:[<span class="DATA" id="lblChangeMail">7310 DENNISTON AVE <br/>PITTSBURGH , PA 15218-2527</span>]
['7310\xa0DENNISTON\xa0AVE\xa0', <br/>, 'PITTSBURGH\xa0,\xa0PA\xa015218-2527']
dgjalksdjgdsag
7310 DENNISTON AVE
city:PITTSBURGH 
state:PA
zip:15218
ARE THEY THE SAME??? True7310 DENNISTON AVE7310 DENNISTON AVE
{'street': '7310 DENNISTON AVE', 'city': 'PITTSBURGH', 'state': 'PA', 'zipc': '15218'}
SAME ADDRESS
None
extracted owner address: 7310 DENNISTON AVE PITTSBURGH , PA 15218
Inserting person data for id: 83533
person notes:In case of confusion, check autm

Scraping data from county: %s0235A00120000000
newid:173544
Scraped:[<span class="Data" id="BasicInfo1_lblAddress">7727 SAINT LAWRENCE  AVE<br/>PITTSBURGH, PA 15218</span>]
7727 SAINT LAWRENCE AVE
city:PITTSBURGH
Zip:15218
Inserting parcelid data: 0235A00120000000
----- committed property core table -----
1
personid:83538
owner_raw_name:MARSHALL BRIAN  &  VICKIE ANN MARSHALL     
extracted owner:MARSHALL BRIAN & VICKIE ANN MARSHALL
--------- extracting owner address ------------
Scraped:[<span class="DATA" id="lblChangeMail">7727 SAINT LAWRENCE AVE <br/>PITTSBURGH , PA 15218-2138</span>]
['7727\xa0SAINT LAWRENCE\xa0AVE\xa0', <br/>, 'PITTSBURGH\xa0,\xa0PA\xa015218-2138']
dgjalksdjgdsag
7727 SAINT LAWRENCE AVE
city:PITTSBURGH 
state:PA
zip:15218
ARE THEY THE SAME??? True7727 SAINT LAWRENCE AVE7727 SAINT LAWRENCE AVE
{'street': '7727 SAINT LAWRENCE AVE', 'city': 'PITTSBURGH', 'state': 'PA', 'zipc': '15218'}
SAME ADDRESS
None
extracted owner address: 7727 SAINT LAWRENCE AVE PITTSBURGH , PA 

Scraping data from county: %s0178E00110000000
newid:173550
Scraped:[<span class="Data" id="BasicInfo1_lblAddress">6907 MCCLURE  AVE<br/>PITTSBURGH, PA 15218</span>]
6907 MCCLURE AVE
city:PITTSBURGH
Zip:15218
Inserting parcelid data: 0178E00110000000
----- committed property core table -----
1
personid:83544
owner_raw_name:LEIGHTY REBECCA M     
extracted owner:LEIGHTY REBECCA M
--------- extracting owner address ------------
Scraped:[<span class="DATA" id="lblChangeMail">261 S PARKVIEW AVE <br/>COLUMBUS , OH 43209-1649</span>]
['261\xa0S\xa0PARKVIEW\xa0AVE\xa0', <br/>, 'COLUMBUS\xa0,\xa0OH\xa043209-1649']
dgjalksdjgdsag
261 S PARKVIEW AVE
city:COLUMBUS 
state:OH
zip:43209
ARE THEY THE SAME??? False261 S PARKVIEW AVE6907 MCCLURE AVE
{'street': '6907 MCCLURE AVE', 'city': 'PITTSBURGH', 'state': 'PA', 'zipc': '15218'}
DIFFERENT MAILING
11
22
None
In case of confusion, check autmated record entry with raw text from the county database:LEIGHTY REBECCA M Raw address: [<span class="DATA" id="

Scraping data from county: %s0177F00134000000
newid:173556
Scraped:[<span class="Data" id="BasicInfo1_lblAddress">TREVANION  AVE<br/>PITTSBURGH, PA 15218</span>]
TREVANION AVE
city:PITTSBURGH
Zip:15218
Inserting parcelid data: 0177F00134000000
----- committed property core table -----
1
personid:83550
owner_raw_name:COMMUNITY LIVING &  SUPPORT SERVICES INC     
extracted owner:COMMUNITY LIVING & SUPPORT SERVICES INC
--------- extracting owner address ------------
Scraped:[<span class="DATA" id="lblChangeMail">4638 CENTRE AVE <br/>PITTSBURGH , PA 15213-1556</span>]
['4638\xa0CENTRE\xa0AVE\xa0', <br/>, 'PITTSBURGH\xa0,\xa0PA\xa015213-1556']
dgjalksdjgdsag
4638 CENTRE AVE
city:PITTSBURGH 
state:PA
zip:15213
ARE THEY THE SAME??? False4638 CENTRE AVETREVANION AVE
{'street': 'TREVANION AVE', 'city': 'PITTSBURGH', 'state': 'PA', 'zipc': '15218'}
DIFFERENT MAILING
11
22
None
In case of confusion, check autmated record entry with raw text from the county database:COMMUNITY LIVING & SUPPORT SERV

ConnectionError: HTTPConnectionPool(host='www2.county.allegheny.pa.us', port=80): Read timed out.